
# Track C – Spatial Grounding

This notebook evaluates **spatial understanding** by detecting and tracking key objects, limbs, or regions over time.  
It demonstrates:

- **Object / body-part detection** (hands, limbs, tools, regions)
- **Pose tracking** using [MediaPipe Pose](https://developers.google.com/mediapipe/solutions/vision/pose)
- **Spatial grounding & overlays** (bounding boxes, keypoints)
- **IoU and positional stability metrics**

### Outputs
- Annotated video with bounding boxes & pose skeletons
- CSV file of IoU & stability metrics


In [ ]:

# --- Setup
!pip install mediapipe ultralytics opencv-python pandas numpy tqdm -q


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 1.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.6/35.6 MB 53.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 66.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.0/63.0 MB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.0/18.0 MB 78.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 22.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 77.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.2/81.2 MB 9.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 MB 10.7 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
grpcio-status 1.71.2 requires protobuf<6.0dev,>=5.26.1, but you have protobuf 4.25.8 which is incompatible.
opentele

In [ ]:
!pip install --upgrade pip setuptools wheel
!pip uninstall -y numpy opencv-python pandas
!pip install numpy==1.26.4 opencv-python==4.9.0.80 pandas==2.2.2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 73.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 70.5 MB/s eta 0:00:00
  Attempting uninstall: setuptools
    Found existing installation: setuptools 75.2.0
    Uninstalling setuptools-75.2.0:
      Successfully uninstalled setuptools-75.2.0
  Attempting uninstall: pip
    Found existing installation: pip 24.1.2
    Uninstalling pip-24.1.2:
      Successfully uninstalled pip-24.1.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
ipython 7.34.0 requires jedi>=0.16, which is not installed.


Found existing installation: numpy 2.0.2
Uninstalling numpy-2.0.2:
  Successfully uninstalled numpy-2.0.2
Found existing installation: opencv-python 4.12.0.88
Uninstalling opencv-python-4.12.0.88:
  Successfully uninstalled opencv-python-4.12.0.88
Found existing installation: pandas 2.2.2
Uninstalling pandas-2.2.2:
  Successfully uninstalled pandas-2.2.2
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.0/18.0 MB 119.0 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.2/62.2 MB 121.2 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.7/12.7 MB 105.1 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3/3 [opencv-python]
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
jaxlib 0.7.2 requires numpy>=2.0, but you have numpy 1.26.4 which is incompatible.
pytensor 2.35.1 requires numpy>=2.0, but you have numpy 1.26.4 which is incompatible.
open

In [ ]:
!pip install numpy==1.26.4 opencv-python==4.9.0.80 pandas==2.2.2 mediapipe==0.10.13 ultralytics tqdm

INFO: pip is looking at multiple versions of jax to determine which version is compatible with other requirements. This could take a while.
INFO: pip is looking at multiple versions of opencv-contrib-python to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.6/35.6 MB 36.4 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 68.8 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 118.5 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.2/81.2 MB 160.1 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 MB 164.0 MB/s  0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.29.5
    Uninstalling protobuf-5.29.5:
      Successfully uninstalled protobuf-5.29.5
  Attempting uninstall: opencv-contrib-python
    Found existing installation: opencv-contrib-python 4.12.0.88
    Uninstalling opencv-contrib-python-4.12.0.88:

In [ ]:
import cv2, mediapipe as mp, numpy as np, pandas as pd, os
from tqdm import tqdm
from ultralytics import YOLO
from IPython.display import Video, display

# Initialize detectors
mp_pose = mp.solutions.pose
pose = mp_pose.Pose(static_image_mode=False, min_detection_confidence=0.5, min_tracking_confidence=0.5)

# Load lightweight YOLO model (CPU)
try:
    yolo = YOLO('yolov8n.pt')
except Exception as e:
    print("Warning: YOLOv8 not found or incompatible:", e)
    yolo = None

os.makedirs("trackC_outputs", exist_ok=True)

NameError: name 'core' is not defined

In [ ]:
# Uninstall potentially conflicting packages
!pip uninstall -y mediapipe numpy opencv-python pandas jax jaxlib protobuf ultralytics ultralytics-thop sounddevice

Found existing installation: mediapipe 0.10.13
Uninstalling mediapipe-0.10.13:
  Successfully uninstalled mediapipe-0.10.13
Found existing installation: numpy 1.26.4
Uninstalling numpy-1.26.4:
  Successfully uninstalled numpy-1.26.4
Found existing installation: opencv-python 4.9.0.80
Uninstalling opencv-python-4.9.0.80:
  Successfully uninstalled opencv-python-4.9.0.80
Found existing installation: pandas 2.2.2
Uninstalling pandas-2.2.2:
  Successfully uninstalled pandas-2.2.2
Found existing installation: jax 0.7.1
Uninstalling jax-0.7.1:
  Successfully uninstalled jax-0.7.1
Found existing installation: jaxlib 0.7.1
Uninstalling jaxlib-0.7.1:
  Successfully uninstalled jaxlib-0.7.1
Found existing installation: protobuf 4.25.8
Uninstalling protobuf-4.25.8:
  Successfully uninstalled protobuf-4.25.8
Found existing installation: ultralytics 8.3.228
Uninstalling ultralytics-8.3.228:
  Successfully uninstalled ultralytics-8.3.228
Found existing installation: ultralytics-thop 2.0.18
Uninstall

In [ ]:
# Reinstall packages with specified versions
!pip install numpy==1.26.4 opencv-python==4.9.0.80 pandas==2.2.2 mediapipe==0.10.13 ultralytics tqdm

In [ ]:
import cv2, mediapipe as mp, numpy as np, pandas as pd, os
from tqdm import tqdm
from ultralytics import YOLO
from IPython.display import Video, display

# Initialize detectors
mp_pose = mp.solutions.pose
pose = mp_pose.Pose(static_image_mode=False, min_detection_confidence=0.5, min_tracking_confidence=0.5)

# Load lightweight YOLO model (CPU)
try:
    yolo = YOLO('yolov8n.pt')
except Exception as e:
    print("Warning: YOLOv8 not found or incompatible:", e)
    yolo = None

os.makedirs("trackC_outputs", exist_ok=True)

/usr/local/lib/python3.12/dist-packages/jaxlib/plugin_support.py:71: RuntimeWarning: JAX plugin jax_cuda12_plugin version 0.7.2 is installed, but it is not compatible with the installed jaxlib version 0.7.1, so it will not be used.
  warnings.warn(


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


## 1. Load or capture video

In [ ]:

video_path = "/content/irma_satellite_simulation.mp4"  # Replace with your file path or 0 for webcam

cap = cv2.VideoCapture(video_path)
if not cap.isOpened():
    raise RuntimeError(f"Cannot open video source: {video_path}")

fps = cap.get(cv2.CAP_PROP_FPS) or 30.0
W = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
H = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

out_path = "trackC_outputs/spatial_grounding_annotated.mp4"
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
writer = cv2.VideoWriter(out_path, fourcc, fps, (W, H))

frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
print(f"Video loaded: {frames} frames at {fps:.1f} FPS, size=({W}x{H})")


Video loaded: 480 frames at 24.0 FPS, size=(640x480)


## 2. Process frames for spatial grounding

In [ ]:

iou_values, stability_values = [], []
prev_boxes, prev_centroids = None, []

for i in tqdm(range(frames)):
    ret, frame = cap.read()
    if not ret: break
    rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)

    # --- Pose Detection
    pose_res = pose.process(rgb)
    if pose_res.pose_landmarks:
        for lm in pose_res.pose_landmarks.landmark:
            cx, cy = int(lm.x * W), int(lm.y * H)
            cv2.circle(frame, (cx, cy), 3, (0,255,255), -1)
        mp.solutions.drawing_utils.draw_landmarks(frame, pose_res.pose_landmarks, mp_pose.POSE_CONNECTIONS)

    # --- Object Detection (YOLO)
    boxes = []
    if yolo:
        results = yolo.predict(frame, imgsz=320, verbose=False)
        for r in results:
            for box in r.boxes.xyxy.cpu().numpy():
                x1,y1,x2,y2 = box[:4].astype(int)
                boxes.append((x1,y1,x2,y2))
                cv2.rectangle(frame,(x1,y1),(x2,y2),(0,255,0),2)

    # --- IoU Calculation (frame-to-frame overlap)
    if prev_boxes and boxes:
        inter_areas = []
        for (x1,y1,x2,y2) in boxes:
            for (px1,py1,px2,py2) in prev_boxes:
                ix1,iy1,ix2,iy2 = max(x1,px1), max(y1,py1), min(x2,px2), min(y2,py2)
                if ix2>ix1 and iy2>iy1:
                    inter = (ix2-ix1)*(iy2-iy1)
                    union = (x2-x1)*(y2-y1)+(px2-px1)*(py2-py1)-inter
                    inter_areas.append(inter/union if union>0 else 0)
        if inter_areas:
            iou_values.append(np.mean(inter_areas))

    # --- Positional stability (centroid movement)
    if boxes:
        centroids = [(int((x1+x2)/2), int((y1+y2)/2)) for (x1,y1,x2,y2) in boxes]
        if prev_centroids:
            dists = [np.linalg.norm(np.array(c1)-np.array(c2)) for c1,c2 in zip(centroids, prev_centroids[:len(centroids)])]
            stability_values.append(np.mean(dists))
        prev_centroids = centroids

    prev_boxes = boxes
    writer.write(frame)

cap.release()
writer.release()


100%|██████████| 480/480 [00:15<00:00, 30.49it/s]


## 3. Compute metrics and visualize results

In [ ]:

mean_iou = np.mean(iou_values) if iou_values else 0
mean_stability = np.mean(stability_values) if stability_values else 0

metrics = {
    "mean_IoU": mean_iou,
    "mean_stability": mean_stability,
    "num_frames": frames
}
df = pd.DataFrame([metrics])
df.to_csv("trackC_outputs/trackC_spatial_metrics.csv", index=False)
print("Metrics saved:", df)

display(Video(out_path, embed=True, width=480))


Metrics saved:    mean_IoU  mean_stability  num_frames
0  0.995704        0.585429         480


✅ **Results Summary**

In [ ]:

print(df.to_string(index=False))


 mean_IoU  mean_stability  num_frames
 0.995704        0.585429         480
